In [1]:
import smtplib
from email.mime.text import MIMEText
from email.mime.multipart import MIMEMultipart
from email.mime.application import MIMEApplication
from email.header import Header

In [2]:
from exctractGsheet import getDataFrameFromGsheet
from prepareData import getSlots, getCalendarObject,getCalendarObjects, getHTMLcontent, getHTMLhome
from sms import prepare_sms

In [3]:
import os
import warnings
import locale
import traceback
import codecs
import datetime
import pandas as pd
from typing import List
locale.setlocale(locale.LC_ALL, 'FR_fr')

'FR_fr'

In [4]:
OUTPUT_FOLDER = "output"
ALARM_DB = os.path.join(OUTPUT_FOLDER,"alarms.feather")

In [5]:
doc_uuid = "1iSA5LsNdarYqrZRxE76lE2VkEsoQksIu6rFG7VAfCNQ"
planning_gid = "1001381542"
creneau_gid = "1884137958"
benevole_gid_2021 = "2065754071"
benevole_gid_2022 = "82247394"

doc_uuid_2021 = "1OO8jyb4_MWFgqVPlTIqePcwkA3sC5WqhsddDMkvIczE" 

In [6]:
def getEmail(name, df_contact):
    idx = df_contact["Prénom"]==name
    if idx.count()==0:
        raise KeyError("User "+ name + "not found in the contact list")
    else:
        return df_contact.Mail[idx].item()
        
def getPhone(name, df_contact):
    idx = df_contact["Prénom"]==name
    if idx.count()==0:
        raise KeyError("User "+ name + "not found in the contact list")
    else:
        return df_contact["Tél"][idx].item()
    
def sendEmailWithAttachment(smtp_server, user:str, to:str, subject:str, body:str, attachement_name:str,attachement_content:str):
    # create message object
    message = MIMEMultipart()
 
    # add in header
    message['From'] = Header(user)
    message['To'] = Header(to)
    message['Subject'] = Header(subject)
 
    # attach message body as MIMEText
    message.attach(MIMEText(body, 'html', 'utf-8'))
    
    def attachContent(content,filename):
        att = MIMEApplication(content, _subtype="txt")
        att.add_header('Content-Disposition', 'attachment', filename=filename)
        message.attach(att)
    
    if isinstance(attachement_content,list):
        for idx, c in enumerate(attachement_content):
            attachContent(c,attachement_name.replace(".",f"{idx:20.0f}."))
    else:
        attachContent(attachement_content,attachement_name)
        
    smtp_server.sendmail(user, to, message.as_string())

In [7]:
# Gather data
df_planning, df_creneau,df_contact = getDataFrameFromGsheet(doc_uuid,benevole_id=benevole_gid_2022,suffix="_2022",starting_date=datetime.datetime(2022, 9, 8))

# Setup mail service
username = "clovis@jaquin.fr"

smtp_server=smtplib.SMTP("smtp.jaquin.fr",587)
smtp_server.ehlo() #setting the ESMTP protocol
smtp_server.starttls() #setting up to TlS connection
smtp_server.ehlo() #calling the ehlo() again as encryption happens on calling startttls()

smtp_server.login(username,"2904Pap1961")

531 créneaux trouvés


(235, b'2.7.0 Authentication successful')

In [8]:
reminders_sms = []
web_pages = []
if not os.path.exists(OUTPUT_FOLDER):
  os.mkdir(OUTPUT_FOLDER)
  
WEB_FOLDER = os.path.join(OUTPUT_FOLDER,"web")
if not os.path.exists(WEB_FOLDER):
  os.mkdir(WEB_FOLDER)

for name in df_planning.benevole_nom.unique():
    # if name!="Clovis":
    #     continue
    try:
        email = getEmail(name,df_contact)
        phone_number = getPhone(name, df_contact)
        fname = email.split("@")[0]+".html"

        slots = getSlots(name, df_planning, df_contact, df_creneau)
        # Generate SMS alarms to be send to 
        for slot in slots:
          SMS_alarm = {"phone_number":phone_number,"time":slot.alarm_time,"content":slot.toReminderText() , 'is_sent':False}
          reminders_sms.append(SMS_alarm)
        new_calendar = getCalendarObjects(slots)

        # Create email to communicate slots to benevole
        html_mail = getHTMLcontent(slots, name, True)
        
        with warnings.catch_warnings():
          warnings.simplefilter("ignore")
          attachement = [c.serialize() for c in new_calendar]
        with codecs.open(os.path.join(OUTPUT_FOLDER,fname),"w","utf-8") as f:
          f.write(html_mail)
        # sendEmailWithAttachment(smtp_server,username,email,"[BDLG 2021] Créneaux Bénévoles",html,"BDLG2021.ics",attachement)
    
        # Create Web page for display 
        html = getHTMLcontent(slots, name, False)
        with codecs.open(os.path.join(WEB_FOLDER,fname),"w","utf-8") as f:
          f.write(html)

        web_pages.append((name[0].upper()+name[1:].lower(),fname))
        
    except Exception as e:
        print("Erreur lors du traitement du bénévole " + name)
        traceback.print_exception(e)

web_pages.sort()
with codecs.open(os.path.join(WEB_FOLDER,"index.html"),"w","utf-8") as f:
    f.write(getHTMLhome(web_pages))
          
df_alarms = pd.DataFrame(reminders_sms)
df_alarms.to_feather(ALARM_DB)

In [9]:
with codecs.open(os.path.join(WEB_FOLDER,"index.html"),"w","utf-8") as f:
    f.write(getHTMLhome(web_pages))

In [13]:
import random
import datetime

def generateFakeAlarms(phone_numbers:List[str],start_time:datetime.datetime, n:int):
  records = []
  DELTA = datetime.timedelta(minutes=30)
  next_alarm = start_time 
  for i in range(n):
    records.append({
      'phone_number':random.choice(phone_numbers),
      "time":next_alarm,
      "content":"Coucou,\nton créneau bénévole commence bientôt : " + next_alarm.strftime("%Hh%M"),
      "is_sent":False
    })
    next_alarm += DELTA
  return pd.DataFrame.from_dict(records)

df_fake_alarm = generateFakeAlarms(["0668798673"],datetime.datetime.now(),10)
df_fake_alarm.to_feather(ALARM_DB)
df_fake_alarm


phone_number                       time  \
0   0668798673 2022-09-06 22:27:05.050516   
1   0668798673 2022-09-06 22:57:05.050516   
2   0668798673 2022-09-06 23:27:05.050516   
3   0668798673 2022-09-06 23:57:05.050516   
4   0668798673 2022-09-07 00:27:05.050516   
5   0668798673 2022-09-07 00:57:05.050516   
6   0668798673 2022-09-07 01:27:05.050516   
7   0668798673 2022-09-07 01:57:05.050516   
8   0668798673 2022-09-07 02:27:05.050516   
9   0668798673 2022-09-07 02:57:05.050516   

                                             content  is_sent  
0  Coucou,\nton créneau bénévole commence bientôt...    False  
1  Coucou,\nton créneau bénévole commence bientôt...    False  
2  Coucou,\nton créneau bénévole commence bientôt...    False  
3  Coucou,\nton créneau bénévole commence bientôt...    False  
4  Coucou,\nton créneau bénévole commence bientôt...    False  
5  Coucou,\nton créneau bénévole commence bientôt...    False  
6  Coucou,\nton créneau bénévole commence bientôt...    False  
7  Coucou,\nton créneau bénévole commence bientôt...    False  
8  Coucou,\nton créneau bénévole commence bientôt...    False  
9  Coucou,\nton créneau bénévole commence bientôt...    False

In [21]:
pd.read_feather(ALARM_DB)

phone_number                       time  \
0   0668798673 2022-09-05 18:17:32.915774   
1   0668798673 2022-09-05 18:47:32.915774   
2   0668798673 2022-09-05 19:17:32.915774   
3   0668798673 2022-09-05 19:47:32.915774   
4   0668798673 2022-09-05 20:17:32.915774   
5   0668798673 2022-09-05 20:47:32.915774   
6   0668798673 2022-09-05 21:17:32.915774   
7   0668798673 2022-09-05 21:47:32.915774   
8   0668798673 2022-09-05 22:17:32.915774   
9   0668798673 2022-09-05 22:47:32.915774   

                                             content  is_sent  
0  Coucou,\nton créneau bénévole commence bientôt...     True  
1  Coucou,\nton créneau bénévole commence bientôt...     True  
2  Coucou,\nton créneau bénévole commence bientôt...     True  
3  Coucou,\nton créneau bénévole commence bientôt...     True  
4  Coucou,\nton créneau bénévole commence bientôt...     True  
5  Coucou,\nton créneau bénévole commence bientôt...     True  
6  Coucou,\nton créneau bénévole commence bientôt...     True  
7  Coucou,\nton créneau bénévole commence bientôt...     True  
8  Coucou,\nton créneau bénévole commence bientôt...     True  
9  Coucou,\nton créneau bénévole commence bientôt...     True

In [ ]:
# Clear setup
smtp_server.quit()

In [9]:
name= "Clovis"
phone_number = getPhone(name,df_contact) 
slots = getSlots(name,df_planning,df_contact,df_creneau)

AttributeError: module 'pandas' has no attribute 'from_dict'

In [14]:

from jinja2 import Environment, FileSystemLoader, select_autoescape
import IPython
JINJA_ENV = Environment(
    loader=FileSystemLoader("templates"),
    autoescape=select_autoescape()
)

In [15]:
template = JINJA_ENV.get_template("Creneau.html")
IPython.display.HTML(template.render(slot=slots[0]))

In [22]:
template_planning = JINJA_ENV.get_template("Calendar.html")

In [23]:
html = template_planning.render(slots=slots)
IPython.display.HTML(html)

In [ ]:

def getCalendarObject(name:str,df:pd.DataFrame)->ics.Calendar:
    new_calendar = ics.Calendar(creator=PROGRAM_UID)
    for row, item in df[df.benevole_nom ==name].iterrows():
        starting_with_you = df.benevole_nom[(df.nom==item.nom) & (df.start==item.start) & (df.benevole_nom!=name)]

        benevole_you_replace = df.benevole_nom[(df.nom==item.nom) & (df.end==item.start)]

        benevole_following_you = df.benevole_nom[(df.nom==item.nom) & (df.start==item.end)]

        creneau_detail = df_creneau[df_creneau.nom==item.nom]
        description = ""
        location = "undefined"
        if len(creneau_detail) >0:
            creneau = creneau.iloc[0]
            description = f"""{creneau.description} 

    Responsable à contacter en cas de problème : {creneau.responsable}"""
            location = creneau.lieu

        if len(starting_with_you)>0:
            description+= "\n\nLes bénévoles avec qui tu sera : "+BENEVOLE_SEPARATOR.join(["",*getContactList(starting_with_you, df_contact)])

        if len(benevole_you_replace)>0:
            description+= "\n\nLes bénévoles que tu remplaces : " +BENEVOLE_SEPARATOR.join(["",*getContactList(benevole_you_replace, df_contact)])

        if len(benevole_following_you)>0:
            description+= "\n\nLes personnes qui arrivent après toi : "+BENEVOLE_SEPARATOR.join(["",*getContactList(benevole_following_you, df_contact)])

        alarms = [ics.AudioAlarm(ALARM_DELTA),ics.DisplayAlarm(ALARM_DELTA)]
        event = ics.Event(name=f"[BDLG] {item.nom}",begin =item.start,end=item.end,description=description,location = location,
                         alarms=alarms)


        new_calendar.events.add(event)
    return new_calendar